In [1]:
!pip install pymongo pandas


[notice] A new release of pip is available: 23.1.2 -> 23.3.2
[notice] To update, run: python -m pip install --upgrade pip


In [2]:
from pymongo import MongoClient
import pandas as pd

In [3]:
client = MongoClient("mongodb://localhost")
client

MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True)

In [4]:
client.list_database_names()

['admin', 'config', 'local', 'network_report']

In [5]:
db = client.network_report

In [6]:
db.list_collection_names()

['exfo_api', 'mascot']

In [7]:
all_result = list(db['exfo_api'].find({'ids.sla_id': 1350}))
all_df = pd.DataFrame(all_result)
all_df

_id  \
0    65893c1d178d19558e1be8fb   
1    65893c1f178d19558e1be902   
2    65895ea2b6630cab2c9aebde   
3    65895ea4071ee1d4559aebde   
4    65895edfed1cfbcda79aebde   
..                        ...   
211  65899098b6630cab2c9af4d8   
212  658990de071ee1d4559af486   
213  65899123b6630cab2c9af4ee   
214  65899159ed1cfbcda79aec4c   
215  65899190071ee1d4559af49c   

                                                   ids  \
0    {'cur_sla_version': 571, 'cur_sla_version_uri'...   
1    {'cur_sla_version': 571, 'cur_sla_version_uri'...   
2    {'cur_sla_version': 571, 'cur_sla_version_uri'...   
3    {'cur_sla_version': 571, 'cur_sla_version_uri'...   
4    {'cur_sla_version': 571, 'cur_sla_version_uri'...   
..                                                 ...   
211  {'cur_sla_version': 574, 'cur_sla_version_uri'...   
212  {'cur_sla_version': 574, 'cur_sla_version_uri'...   
213  {'cur_sla_version': 574, 'cur_sla_version_uri'...   
214  {'cur_sla_version': 574, 'cur_sla_version_uri'...   
215  {'cur_sla_version': 574, 'cur_sla_version_uri'...   

                                        sla_uri_result  \
0    {'attributes': {'author': 'administrator', 'bi...   
1    {'attributes': {'author': 'administrator', 'bi...   
2    {'attributes': {'author': 'administrator', 'bi...   
3    {'attributes': {'author': 'administrator', 'bi...   
4    {'attributes': {'author': 'administrator', 'bi...   
..                                                 ...   
211  {'attributes': {'author': 'administrator', 'bi...   
212  {'attributes': {'author': 'administrator', 'bi...   
213  {'attributes': {'author': 'administrator', 'bi...   
214  {'attributes': {'author': 'administrator', 'bi...   
215  {'attributes': {'author': 'administrator', 'bi...   

                            test_instance_class_result  \
0    [{'config': {'interface_categories': [{'name':...   
1    [{'config': {'interface_categories': [{'name':...   
2                                                   []   
3                                                   []   
4                                                   []   
..                                                 ...   
211                                                 []   
212                                                 []   
213                                                 []   
214                                                 []   
215                                                 []   

                                    test_status_result                 created  
0    [{'sla_name': 'POC-Expansion-SLA_BRAS_88_Priva... 2023-12-25 08:23:57.676  
1    [{'sla_name': 'POC-Expansion-SLA_BRAS_88_Priva... 2023-12-25 08:23:59.615  
2                                                   [] 2023-12-25 10:51:14.829  
3                                                   [] 2023-12-25 10:51:16.702  
4                                                   [] 2023-12-25 10:52:15.282  
..                                                 ...                     ...  
211                                                 [] 2023-12-25 14:24:24.588  
212                                                 [] 2023-12-25 14:25:34.871  
213                                                 [] 2023-12-25 14:26:43.482  
214                                                 [] 2023-12-25 14:27:37.016  
215                                                 [] 2023-12-25 14:28:32.700  

[216 rows x 6 columns]

In [8]:
r0 = list(db['exfo_api'].find().sort("created", -1).limit(30))
pd.json_normalize(r0, ['test_status_result','status', 'results_scores'], ['test_status_result','test_instance_id'], errors='ignore')

name  raw_value  score  \
0      totalPageDownloadTime   203061.0  100.0   
1                     result      100.0  100.0   
2      totalPageDownloadTime        NaN    NaN   
3                     result        NaN    NaN   
4                     result      100.0  100.0   
...                      ...        ...    ...   
43831    endToEndDelayMedian        NaN    NaN   
43832                 result        NaN    NaN   
43833                 result      100.0  100.0   
43834     percentLostPackets       40.0   80.0   
43835    endToEndDelayMedian     5698.5  100.0   

                                      test_status_result test_instance_id  
0      [{'sla_name': 'BV110_CMI', 'test_instance_id':...              NaN  
1      [{'sla_name': 'BV110_CMI', 'test_instance_id':...              NaN  
2      [{'sla_name': 'BV110_CMI', 'test_instance_id':...              NaN  
3      [{'sla_name': 'BV110_CMI', 'test_instance_id':...              NaN  
4      [{'sla_name': 'BV110_CMI', 'test_instance_id':...              NaN  
...                                                  ...              ...  
43831  [{'sla_name': 'BV110_PTY', 'test_instance_id':...              NaN  
43832  [{'sla_name': 'BV110_PTY', 'test_instance_id':...              NaN  
43833  [{'sla_name': 'BV110_PTY', 'test_instance_id':...              NaN  
43834  [{'sla_name': 'BV110_PTY', 'test_instance_id':...              NaN  
43835  [{'sla_name': 'BV110_PTY', 'test_instance_id':...              NaN  

[43836 rows x 5 columns]

In [30]:
from pprint import pprint
list_test_status_result = list(db['exfo_api'].find({}, {'test_status_result':1, 'ids': 1}).sort("created", -1).skip(1000).limit(500))
print(len(list_test_status_result))
data = []
data2 = []
for l in list_test_status_result:
    data = data + l['test_status_result']
    data2.append(l['ids'])
print(len(data))
print(len(data2))

500
5394
500


In [31]:
df0 = pd.json_normalize(data)
df0
print(len(data))

5394


In [32]:
df0['sla_name'].unique()

array(['BV110_NMA', 'BV110_PLK', 'BV110_KKN', 'BV110_RBI', 'BV110_HYI',
       'BV110_SNI', 'BV1100_BRK', 'BV110_PTY', 'ATP-Expansion BRIX',
       'BV110_CMI', 'BV110_NWS',
       'POC-Expansion-SLA_BNG_144_Private (VLAN10)',
       'POC-Expansion-SLA_BRAS_88_Public (VLAN20)'], dtype=object)

In [33]:
df0['sla_name'].unique()

array(['BV110_NMA', 'BV110_PLK', 'BV110_KKN', 'BV110_RBI', 'BV110_HYI',
       'BV110_SNI', 'BV1100_BRK', 'BV110_PTY', 'ATP-Expansion BRIX',
       'BV110_CMI', 'BV110_NWS',
       'POC-Expansion-SLA_BNG_144_Private (VLAN10)',
       'POC-Expansion-SLA_BRAS_88_Public (VLAN20)'], dtype=object)

In [34]:
len(data2)

500

In [35]:
df_ids = pd.json_normalize(data2)
df_ids

cur_sla_version                     cur_sla_version_uri  sla_id  \
0                 29   /API/REST/SLAs/v1/SLA/1150/Version/29    1150   
1                 20   /API/REST/SLAs/v1/SLA/1125/Version/20    1125   
2                 71   /API/REST/SLAs/v1/SLA/1034/Version/71    1034   
3                 73   /API/REST/SLAs/v1/SLA/1026/Version/73    1026   
4                 75   /API/REST/SLAs/v1/SLA/1033/Version/75    1033   
..               ...                                     ...     ...   
495              574  /API/REST/SLAs/v1/SLA/1350/Version/574    1350   
496               29   /API/REST/SLAs/v1/SLA/1150/Version/29    1150   
497               20   /API/REST/SLAs/v1/SLA/1125/Version/20    1125   
498               71   /API/REST/SLAs/v1/SLA/1034/Version/71    1034   
499               73   /API/REST/SLAs/v1/SLA/1026/Version/73    1026   

                                       sla_name  \
0                                  ppp-vlan-999   
1                          BV110_PCB pppoe test   
2                                     BV110_NMA   
3                                     BV110_PLK   
4                                     BV110_KKN   
..                                          ...   
495  POC-Expansion-SLA_BRAS_88_Private (VLAN10)   
496                                ppp-vlan-999   
497                        BV110_PCB pppoe test   
498                                   BV110_NMA   
499                                   BV110_PLK   

                         sla_status_uri                     sla_uri  
0    /API/REST/Status/v1/SLAStatus/1150  /API/REST/SLAs/v1/SLA/1150  
1    /API/REST/Status/v1/SLAStatus/1125  /API/REST/SLAs/v1/SLA/1125  
2    /API/REST/Status/v1/SLAStatus/1034  /API/REST/SLAs/v1/SLA/1034  
3    /API/REST/Status/v1/SLAStatus/1026  /API/REST/SLAs/v1/SLA/1026  
4    /API/REST/Status/v1/SLAStatus/1033  /API/REST/SLAs/v1/SLA/1033  
..                                  ...                         ...  
495  /API/REST/Status/v1/SLAStatus/1350  /API/REST/SLAs/v1/SLA/1350  
496  /API/REST/Status/v1/SLAStatus/1150  /API/REST/SLAs/v1/SLA/1150  
497  /API/REST/Status/v1/SLAStatus/1125  /API/REST/SLAs/v1/SLA/1125  
498  /API/REST/Status/v1/SLAStatus/1034  /API/REST/SLAs/v1/SLA/1034  
499  /API/REST/Status/v1/SLAStatus/1026  /API/REST/SLAs/v1/SLA/1026  

[500 rows x 6 columns]

In [36]:
df = pd.json_normalize(data, record_path=['status', 'results_scores'], 
                       meta=['test_instance_id', ['status','time_stamp_display']],  errors='ignore')
df

name  raw_value  score test_instance_id  \
0        totalPageDownloadTime   255083.0  100.0            53024   
1                       result      100.0  100.0            53024   
2                       result      100.0  100.0            53024   
3        totalPageDownloadTime   385728.0  100.0            53024   
4                       result      100.0  100.0            53024   
...                        ...        ...    ...              ...   
1014167    endToEndDelayMedian        NaN    NaN            53037   
1014168     percentLostPackets        NaN    NaN            53037   
1014169                 result        NaN    NaN            53037   
1014170    endToEndDelayMedian        NaN    NaN            53037   
1014171     percentLostPackets        NaN    NaN            53037   

        status.time_stamp_display  
0            12/25/2023 13:00 +07  
1            12/25/2023 13:00 +07  
2            12/24/2023 07:00 +07  
3            12/24/2023 07:00 +07  
4            12/23/2023 01:00 +07  
...                           ...  
1014167      12/24/2023 19:45 +07  
1014168      12/24/2023 19:45 +07  
1014169      12/24/2023 19:30 +07  
1014170      12/24/2023 19:30 +07  
1014171      12/24/2023 19:30 +07  

[1014172 rows x 5 columns]

In [37]:
df3 = pd.merge(df0, df, on='test_instance_id')
df3

sla_name test_instance_id  \
0                                         BV110_NMA            53024   
1                                         BV110_NMA            53024   
2                                         BV110_NMA            53024   
3                                         BV110_NMA            53024   
4                                         BV110_NMA            53024   
...                                             ...              ...   
23512650  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512651  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512652  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512653  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512654  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   

                            type_type_name  test_instance_class_id  \
0         com.brixnet.securehttpactivetest                   17138   
1         com.brixnet.securehttpactivetest                   17138   
2         com.brixnet.securehttpactivetest                   17138   
3         com.brixnet.securehttpactivetest                   17138   
4         com.brixnet.securehttpactivetest                   17138   
...                                    ...                     ...   
23512650        com.brixnet.pingactivetest                   48425   
23512651        com.brixnet.pingactivetest                   48425   
23512652        com.brixnet.pingactivetest                   48425   
23512653        com.brixnet.pingactivetest                   48425   
23512654        com.brixnet.pingactivetest                   48425   

                                                     status  \
0         [{'results_scores': [{'name': 'totalPageDownlo...   
1         [{'results_scores': [{'name': 'totalPageDownlo...   
2         [{'results_scores': [{'name': 'totalPageDownlo...   
3         [{'results_scores': [{'name': 'totalPageDownlo...   
4         [{'results_scores': [{'name': 'totalPageDownlo...   
...                                                     ...   
23512650                                                 []   
23512651                                                 []   
23512652                                                 []   
23512653                                                 []   
23512654                                                 []   

          service.service_id               service.service_name  \
0                       1151             HTTPS Web Performances   
1                       1151             HTTPS Web Performances   
2                       1151             HTTPS Web Performances   
3                       1151             HTTPS Web Performances   
4                       1151             HTTPS Web Performances   
...                      ...                                ...   
23512650                1375  Ping catspeedtest (Public-VLAN20)   
23512651                1375  Ping catspeedtest (Public-VLAN20)   
23512652                1375  Ping catspeedtest (Public-VLAN20)   
23512653                1375  Ping catspeedtest (Public-VLAN20)   
23512654                1375  Ping catspeedtest (Public-VLAN20)   

                                    service.service_uri  \
0          /API/REST/Services/v1/Service/1151/Version/6   
1          /API/REST/Services/v1/Service/1151/Version/6   
2          /API/REST/Services/v1/Service/1151/Version/6   
3          /API/REST/Services/v1/Service/1151/Version/6   
4          /API/REST/Services/v1/Service/1151/Version/6   
...                                                 ...   
23512650  /API/REST/Services/v1/Service/1375/Version/16   
23512651  /API/REST/Services/v1/Service/1375/Version/16   
23512652  /API/REST/Services/v1/Service/1375/Version/16   
23512653  /API/REST/Services/v1/Service/1375/Version/16   
23512654  /API/REST/Services/v1/Service/1375/Version/16   

          service.service_version service.slt_id target.target_par

In [38]:
df3.drop(['status'], axis=1)

sla_name test_instance_id  \
0                                         BV110_NMA            53024   
1                                         BV110_NMA            53024   
2                                         BV110_NMA            53024   
3                                         BV110_NMA            53024   
4                                         BV110_NMA            53024   
...                                             ...              ...   
23512650  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512651  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512652  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512653  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512654  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   

                            type_type_name  test_instance_class_id  \
0         com.brixnet.securehttpactivetest                   17138   
1         com.brixnet.securehttpactivetest                   17138   
2         com.brixnet.securehttpactivetest                   17138   
3         com.brixnet.securehttpactivetest                   17138   
4         com.brixnet.securehttpactivetest                   17138   
...                                    ...                     ...   
23512650        com.brixnet.pingactivetest                   48425   
23512651        com.brixnet.pingactivetest                   48425   
23512652        com.brixnet.pingactivetest                   48425   
23512653        com.brixnet.pingactivetest                   48425   
23512654        com.brixnet.pingactivetest                   48425   

          service.service_id               service.service_name  \
0                       1151             HTTPS Web Performances   
1                       1151             HTTPS Web Performances   
2                       1151             HTTPS Web Performances   
3                       1151             HTTPS Web Performances   
4                       1151             HTTPS Web Performances   
...                      ...                                ...   
23512650                1375  Ping catspeedtest (Public-VLAN20)   
23512651                1375  Ping catspeedtest (Public-VLAN20)   
23512652                1375  Ping catspeedtest (Public-VLAN20)   
23512653                1375  Ping catspeedtest (Public-VLAN20)   
23512654                1375  Ping catspeedtest (Public-VLAN20)   

                                    service.service_uri  \
0          /API/REST/Services/v1/Service/1151/Version/6   
1          /API/REST/Services/v1/Service/1151/Version/6   
2          /API/REST/Services/v1/Service/1151/Version/6   
3          /API/REST/Services/v1/Service/1151/Version/6   
4          /API/REST/Services/v1/Service/1151/Version/6   
...                                                 ...   
23512650  /API/REST/Services/v1/Service/1375/Version/16   
23512651  /API/REST/Services/v1/Service/1375/Version/16   
23512652  /API/REST/Services/v1/Service/1375/Version/16   
23512653  /API/REST/Services/v1/Service/1375/Version/16   
23512654  /API/REST/Services/v1/Service/1375/Version/16   

          service.service_version service.slt_id target.target_param  \
0                               6           2157                 url   
1                               6           2157                 url   
2                               6           2157                 url   
3                               6           2157                 url   
4                               6           2157                 url   
...                           ...            ...                 ...   
23512650                       16           2631                host   
23512651                       16           2631                host   
23512652                       16           2631                host   
23512653                       16           2631                host   
23512654                       

In [39]:
df3.query('test_instance_class_id == 1554')

sla_name test_instance_id              type_type_name  \
5019318  BV110_RBI            52952  com.brixnet.pingactivetest   
5019319  BV110_RBI            52952  com.brixnet.pingactivetest   
5019320  BV110_RBI            52952  com.brixnet.pingactivetest   
5019321  BV110_RBI            52952  com.brixnet.pingactivetest   
5019322  BV110_RBI            52952  com.brixnet.pingactivetest   
...            ...              ...                         ...   
5192113  BV110_RBI            52952  com.brixnet.pingactivetest   
5192114  BV110_RBI            52952  com.brixnet.pingactivetest   
5192115  BV110_RBI            52952  com.brixnet.pingactivetest   
5192116  BV110_RBI            52952  com.brixnet.pingactivetest   
5192117  BV110_RBI            52952  com.brixnet.pingactivetest   

         test_instance_class_id  \
5019318                    1554   
5019319                    1554   
5019320                    1554   
5019321                    1554   
5019322                    1554   
...                         ...   
5192113                    1554   
5192114                    1554   
5192115                    1554   
5192116                    1554   
5192117                    1554   

                                                    status  \
5019318  [{'results_scores': [{'name': 'result', 'raw_v...   
5019319  [{'results_scores': [{'name': 'result', 'raw_v...   
5019320  [{'results_scores': [{'name': 'result', 'raw_v...   
5019321  [{'results_scores': [{'name': 'result', 'raw_v...   
5019322  [{'results_scores': [{'name': 'result', 'raw_v...   
...                                                    ...   
5192113  [{'results_scores': [{'name': 'percentLostPack...   
5192114  [{'results_scores': [{'name': 'percentLostPack...   
5192115  [{'results_scores': [{'name': 'percentLostPack...   
5192116  [{'results_scores': [{'name': 'percentLostPack...   
5192117  [{'results_scores': [{'name': 'percentLostPack...   

         service.service_id service.service_name  \
5019318                1051            Ping test   
5019319                1051            Ping test   
5019320                1051            Ping test   
5019321                1051            Ping test   
5019322                1051            Ping test   
...                     ...                  ...   
5192113                1051            Ping test   
5192114                1051            Ping test   
5192115                1051            Ping test   
5192116                1051            Ping test   
5192117                1051            Ping test   

                                  service.service_uri  \
5019318  /API/REST/Services/v1/Service/1051/Version/8   
5019319  /API/REST/Services/v1/Service/1051/Version/8   
5019320  /API/REST/Services/v1/Service/1051/Version/8   
5019321  /API/REST/Services/v1/Service/1051/Version/8   
5019322  /API/REST/Services/v1/Service/1051/Version/8   
...                                               ...   
5192113  /API/REST/Services/v1/Service/1051/Version/8   
5192114  /API/REST/Services/v1/Service/1051/Version/8   
5192115  /API/REST/Services/v1/Service/1051/Version/8   
5192116  /API/REST/Services/v1/Service/1051/Version/8   
5192117  /API/REST/Services/v1/Service/1051/Version/8   

         service.service_version service.slt_id target.target_param  \
5019318                        8           2171                host   
5019319                        8           2171                host   
5019320                        8           2171                host   
5019321                        8           2171                host   
5019322                        8           2171                host   
...                          ...            ...                 ...   
5192113                        8           2171                host   
5192114                        8           2171                host   
5192115                        8           2171                host   
5192116            

In [19]:
ping_test = df3.query("`service.service_name` == 'Ping test'").drop(["status"],axis=1)
ping_test

sla_name test_instance_id              type_type_name  \
50784     BV110_NMA            53053  com.brixnet.pingactivetest   
50785     BV110_NMA            53053  com.brixnet.pingactivetest   
50786     BV110_NMA            53053  com.brixnet.pingactivetest   
50787     BV110_NMA            53053  com.brixnet.pingactivetest   
50788     BV110_NMA            53053  com.brixnet.pingactivetest   
...             ...              ...                         ...   
23019594  BV110_NWS            52959  com.brixnet.pingactivetest   
23019595  BV110_NWS            52959  com.brixnet.pingactivetest   
23019596  BV110_NWS            52959  com.brixnet.pingactivetest   
23019597  BV110_NWS            52959  com.brixnet.pingactivetest   
23019598  BV110_NWS            52959  com.brixnet.pingactivetest   

          test_instance_class_id  service.service_id service.service_name  \
50784                      17150                1051            Ping test   
50785                      17150                1051            Ping test   
50786                      17150                1051            Ping test   
50787                      17150                1051            Ping test   
50788                      17150                1051            Ping test   
...                          ...                 ...                  ...   
23019594                   21892                1051            Ping test   
23019595                   21892                1051            Ping test   
23019596                   21892                1051            Ping test   
23019597                   21892                1051            Ping test   
23019598                   21892                1051            Ping test   

                                   service.service_uri  \
50784     /API/REST/Services/v1/Service/1051/Version/8   
50785     /API/REST/Services/v1/Service/1051/Version/8   
50786     /API/REST/Services/v1/Service/1051/Version/8   
50787     /API/REST/Services/v1/Service/1051/Version/8   
50788     /API/REST/Services/v1/Service/1051/Version/8   
...                                                ...   
23019594  /API/REST/Services/v1/Service/1051/Version/8   
23019595  /API/REST/Services/v1/Service/1051/Version/8   
23019596  /API/REST/Services/v1/Service/1051/Version/8   
23019597  /API/REST/Services/v1/Service/1051/Version/8   
23019598  /API/REST/Services/v1/Service/1051/Version/8   

          service.service_version service.slt_id target.target_param  \
50784                           8           2171                host   
50785                           8           2171                host   
50786                           8           2171                host   
50787                           8           2171                host   
50788                           8           2171                host   
...                           ...            ...                 ...   
23019594                        8           2171                host   
23019595                        8           2171                host   
23019596                        8           2171                host   
23019597                        8           2171                host   
23019598                        8           2171                host   

         target.target_value  target                 name  raw_value  score  \
50784                8.8.8.8     NaN   percentLostPackets        0.0  100.0   
50785                8.8.8.8     NaN  endToEndDelayMedian    40983.0   78.0   
50786                8.8.8.8     NaN               result      100.0  100.0   
50787                8.8.8.8     NaN               result      100.0  100.0   
50788                8.8.8.8     NaN  endToEndDelayMedian    40959.0   78.0   
...                      ...     ...                  ...        ...    ...   
23019594       110.78.191.21     NaN  endToEndDelayMedian        NaN    NaN   
23019595       110.78.191.21     NaN   percentLostPackets        NaN    NaN

In [20]:
ping_test.to_excel("ping_test.xlsx")

ValueError: This sheet is too large! Your sheet size is: 4935600, 16 Max sheet size is: 1048576, 16384

In [ ]:
ping_test.dtypes
ping_test.columns

In [ ]:
ping_test["service.service_name"]

In [40]:
df3['status'][0]

[{'results_scores': [{'name': 'totalPageDownloadTime',
    'raw_value': 255083,
    'score': 100},
   {'name': 'result', 'raw_value': 100, 'score': 100}],
  'score': 100,
  'service_id': 1151,
  'service_instance_name': 'HTTPS Web Performances',
  'service_name': 'HTTPS Web Performances',
  'sla_id': 1034,
  'sla_name': 'BV110_NMA',
  'sla_version': 0,
  'sld_id': 4953,
  'slt_id': 2157,
  'slt_instance_id': 1249,
  'slt_version': 6,
  'test_instance_id': 53024,
  'test_status_calculation_interval': 1800,
  'time_stamp': '1703484000000000000',
  'time_stamp_display': '12/25/2023 13:00 +07',
  'verifier_id': 1009},
 {'results_scores': [{'name': 'result', 'raw_value': 100, 'score': 100},
   {'name': 'totalPageDownloadTime', 'raw_value': 385728, 'score': 100}],
  'score': 100,
  'service_id': 1151,
  'service_instance_name': 'HTTPS Web Performances',
  'service_name': 'HTTPS Web Performances',
  'sla_id': 1034,
  'sla_name': 'BV110_NMA',
  'sla_version': 0,
  'sld_id': 4953,
  'slt_id': 2

In [41]:
df3.dtypes

sla_name                      object
test_instance_id              object
type_type_name                object
test_instance_class_id         int64
status                        object
service.service_id             int64
service.service_name          object
service.service_uri           object
service.service_version        int64
service.slt_id                object
target.target_param           object
target.target_value           object
target                       float64
name                          object
raw_value                    float64
score                        float64
status.time_stamp_display     object
dtype: object

In [42]:
df3

sla_name test_instance_id  \
0                                         BV110_NMA            53024   
1                                         BV110_NMA            53024   
2                                         BV110_NMA            53024   
3                                         BV110_NMA            53024   
4                                         BV110_NMA            53024   
...                                             ...              ...   
23512650  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512651  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512652  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512653  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512654  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   

                            type_type_name  test_instance_class_id  \
0         com.brixnet.securehttpactivetest                   17138   
1         com.brixnet.securehttpactivetest                   17138   
2         com.brixnet.securehttpactivetest                   17138   
3         com.brixnet.securehttpactivetest                   17138   
4         com.brixnet.securehttpactivetest                   17138   
...                                    ...                     ...   
23512650        com.brixnet.pingactivetest                   48425   
23512651        com.brixnet.pingactivetest                   48425   
23512652        com.brixnet.pingactivetest                   48425   
23512653        com.brixnet.pingactivetest                   48425   
23512654        com.brixnet.pingactivetest                   48425   

                                                     status  \
0         [{'results_scores': [{'name': 'totalPageDownlo...   
1         [{'results_scores': [{'name': 'totalPageDownlo...   
2         [{'results_scores': [{'name': 'totalPageDownlo...   
3         [{'results_scores': [{'name': 'totalPageDownlo...   
4         [{'results_scores': [{'name': 'totalPageDownlo...   
...                                                     ...   
23512650                                                 []   
23512651                                                 []   
23512652                                                 []   
23512653                                                 []   
23512654                                                 []   

          service.service_id               service.service_name  \
0                       1151             HTTPS Web Performances   
1                       1151             HTTPS Web Performances   
2                       1151             HTTPS Web Performances   
3                       1151             HTTPS Web Performances   
4                       1151             HTTPS Web Performances   
...                      ...                                ...   
23512650                1375  Ping catspeedtest (Public-VLAN20)   
23512651                1375  Ping catspeedtest (Public-VLAN20)   
23512652                1375  Ping catspeedtest (Public-VLAN20)   
23512653                1375  Ping catspeedtest (Public-VLAN20)   
23512654                1375  Ping catspeedtest (Public-VLAN20)   

                                    service.service_uri  \
0          /API/REST/Services/v1/Service/1151/Version/6   
1          /API/REST/Services/v1/Service/1151/Version/6   
2          /API/REST/Services/v1/Service/1151/Version/6   
3          /API/REST/Services/v1/Service/1151/Version/6   
4          /API/REST/Services/v1/Service/1151/Version/6   
...                                                 ...   
23512650  /API/REST/Services/v1/Service/1375/Version/16   
23512651  /API/REST/Services/v1/Service/1375/Version/16   
23512652  /API/REST/Services/v1/Service/1375/Version/16   
23512653  /API/REST/Services/v1/Service/1375/Version/16   
23512654  /API/REST/Services/v1/Service/1375/Version/16   

          service.service_version service.slt_id target.target_par

In [43]:
df3["value_score"] = df[["raw_value","score"]].astype(str).agg("/".join, axis=1)
df3

sla_name test_instance_id  \
0                                         BV110_NMA            53024   
1                                         BV110_NMA            53024   
2                                         BV110_NMA            53024   
3                                         BV110_NMA            53024   
4                                         BV110_NMA            53024   
...                                             ...              ...   
23512650  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512651  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512652  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512653  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512654  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   

                            type_type_name  test_instance_class_id  \
0         com.brixnet.securehttpactivetest                   17138   
1         com.brixnet.securehttpactivetest                   17138   
2         com.brixnet.securehttpactivetest                   17138   
3         com.brixnet.securehttpactivetest                   17138   
4         com.brixnet.securehttpactivetest                   17138   
...                                    ...                     ...   
23512650        com.brixnet.pingactivetest                   48425   
23512651        com.brixnet.pingactivetest                   48425   
23512652        com.brixnet.pingactivetest                   48425   
23512653        com.brixnet.pingactivetest                   48425   
23512654        com.brixnet.pingactivetest                   48425   

                                                     status  \
0         [{'results_scores': [{'name': 'totalPageDownlo...   
1         [{'results_scores': [{'name': 'totalPageDownlo...   
2         [{'results_scores': [{'name': 'totalPageDownlo...   
3         [{'results_scores': [{'name': 'totalPageDownlo...   
4         [{'results_scores': [{'name': 'totalPageDownlo...   
...                                                     ...   
23512650                                                 []   
23512651                                                 []   
23512652                                                 []   
23512653                                                 []   
23512654                                                 []   

          service.service_id               service.service_name  \
0                       1151             HTTPS Web Performances   
1                       1151             HTTPS Web Performances   
2                       1151             HTTPS Web Performances   
3                       1151             HTTPS Web Performances   
4                       1151             HTTPS Web Performances   
...                      ...                                ...   
23512650                1375  Ping catspeedtest (Public-VLAN20)   
23512651                1375  Ping catspeedtest (Public-VLAN20)   
23512652                1375  Ping catspeedtest (Public-VLAN20)   
23512653                1375  Ping catspeedtest (Public-VLAN20)   
23512654                1375  Ping catspeedtest (Public-VLAN20)   

                                    service.service_uri  \
0          /API/REST/Services/v1/Service/1151/Version/6   
1          /API/REST/Services/v1/Service/1151/Version/6   
2          /API/REST/Services/v1/Service/1151/Version/6   
3          /API/REST/Services/v1/Service/1151/Version/6   
4          /API/REST/Services/v1/Service/1151/Version/6   
...                                                 ...   
23512650  /API/REST/Services/v1/Service/1375/Version/16   
23512651  /API/REST/Services/v1/Service/1375/Version/16   
23512652  /API/REST/Services/v1/Service/1375/Version/16   
23512653  /API/REST/Services/v1/Service/1375/Version/16   
23512654  /API/REST/Services/v1/Service/1375/Version/16   

          service.service_version service.slt_id target.target_par

In [44]:
df3

sla_name test_instance_id  \
0                                         BV110_NMA            53024   
1                                         BV110_NMA            53024   
2                                         BV110_NMA            53024   
3                                         BV110_NMA            53024   
4                                         BV110_NMA            53024   
...                                             ...              ...   
23512650  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512651  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512652  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512653  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   
23512654  POC-Expansion-SLA_BRAS_88_Public (VLAN20)            56066   

                            type_type_name  test_instance_class_id  \
0         com.brixnet.securehttpactivetest                   17138   
1         com.brixnet.securehttpactivetest                   17138   
2         com.brixnet.securehttpactivetest                   17138   
3         com.brixnet.securehttpactivetest                   17138   
4         com.brixnet.securehttpactivetest                   17138   
...                                    ...                     ...   
23512650        com.brixnet.pingactivetest                   48425   
23512651        com.brixnet.pingactivetest                   48425   
23512652        com.brixnet.pingactivetest                   48425   
23512653        com.brixnet.pingactivetest                   48425   
23512654        com.brixnet.pingactivetest                   48425   

                                                     status  \
0         [{'results_scores': [{'name': 'totalPageDownlo...   
1         [{'results_scores': [{'name': 'totalPageDownlo...   
2         [{'results_scores': [{'name': 'totalPageDownlo...   
3         [{'results_scores': [{'name': 'totalPageDownlo...   
4         [{'results_scores': [{'name': 'totalPageDownlo...   
...                                                     ...   
23512650                                                 []   
23512651                                                 []   
23512652                                                 []   
23512653                                                 []   
23512654                                                 []   

          service.service_id               service.service_name  \
0                       1151             HTTPS Web Performances   
1                       1151             HTTPS Web Performances   
2                       1151             HTTPS Web Performances   
3                       1151             HTTPS Web Performances   
4                       1151             HTTPS Web Performances   
...                      ...                                ...   
23512650                1375  Ping catspeedtest (Public-VLAN20)   
23512651                1375  Ping catspeedtest (Public-VLAN20)   
23512652                1375  Ping catspeedtest (Public-VLAN20)   
23512653                1375  Ping catspeedtest (Public-VLAN20)   
23512654                1375  Ping catspeedtest (Public-VLAN20)   

                                    service.service_uri  \
0          /API/REST/Services/v1/Service/1151/Version/6   
1          /API/REST/Services/v1/Service/1151/Version/6   
2          /API/REST/Services/v1/Service/1151/Version/6   
3          /API/REST/Services/v1/Service/1151/Version/6   
4          /API/REST/Services/v1/Service/1151/Version/6   
...                                                 ...   
23512650  /API/REST/Services/v1/Service/1375/Version/16   
23512651  /API/REST/Services/v1/Service/1375/Version/16   
23512652  /API/REST/Services/v1/Service/1375/Version/16   
23512653  /API/REST/Services/v1/Service/1375/Version/16   
23512654  /API/REST/Services/v1/Service/1375/Version/16   

          service.service_version service.slt_id target.target_par

In [45]:
print(df3.query("sla_name == 'BV110_RBI'"))
print(df3["sla_name"].unique())

          sla_name test_instance_id              type_type_name  \
5019318  BV110_RBI            52952  com.brixnet.pingactivetest   
5019319  BV110_RBI            52952  com.brixnet.pingactivetest   
5019320  BV110_RBI            52952  com.brixnet.pingactivetest   
5019321  BV110_RBI            52952  com.brixnet.pingactivetest   
5019322  BV110_RBI            52952  com.brixnet.pingactivetest   
...            ...              ...                         ...   
6776689  BV110_RBI            52983  com.brixnet.pingactivetest   
6776690  BV110_RBI            52983  com.brixnet.pingactivetest   
6776691  BV110_RBI            52983  com.brixnet.pingactivetest   
6776692  BV110_RBI            52983  com.brixnet.pingactivetest   
6776693  BV110_RBI            52983  com.brixnet.pingactivetest   

         test_instance_class_id  \
5019318                    1554   
5019319                    1554   
5019320                    1554   
5019321                    1554   
5019322             

In [46]:
df4 = df3.query("sla_name in ('POC-Expansion-SLA_BRAS_88_Private (VLAN10)','POC-Expansion-SLA_BNG_144_Public (VLAN20)','POC-Expansion-SLA_BNG_144_Private (VLAN10)')")
df4

sla_name test_instance_id  \
23512079  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56068   
23512080  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56068   
23512081  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56068   
23512082  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56068   
23512083  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56068   
...                                              ...              ...   
23512164  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56069   
23512165  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56069   
23512166  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56069   
23512167  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56069   
23512168  POC-Expansion-SLA_BNG_144_Private (VLAN10)            56069   

                      type_type_name  test_instance_class_id  \
23512079  com.brixnet.pingactivetest                   30286   
23512080  com.brixnet.pingactivetest                   30286   
23512081  com.brixnet.pingactivetest                   30286   
23512082  com.brixnet.pingactivetest                   30286   
23512083  com.brixnet.pingactivetest                   30286   
...                              ...                     ...   
23512164  com.brixnet.pingactivetest                   44133   
23512165  com.brixnet.pingactivetest                   44133   
23512166  com.brixnet.pingactivetest                   44133   
23512167  com.brixnet.pingactivetest                   44133   
23512168  com.brixnet.pingactivetest                   44133   

                                                     status  \
23512079  [{'results_scores': [{'name': 'percentLostPack...   
23512080  [{'results_scores': [{'name': 'percentLostPack...   
23512081  [{'results_scores': [{'name': 'percentLostPack...   
23512082                                                 []   
23512083                                                 []   
...                                                     ...   
23512164                                                 []   
23512165                                                 []   
23512166                                                 []   
23512167                                                 []   
23512168                                                 []   

          service.service_id                service.service_name  \
23512079                1376  Ping catspeedtest (Private-VLAN10)   
23512080                1376  Ping catspeedtest (Private-VLAN10)   
23512081                1376  Ping catspeedtest (Private-VLAN10)   
23512082                1376  Ping catspeedtest (Private-VLAN10)   
23512083                1376  Ping catspeedtest (Private-VLAN10)   
...                      ...                                 ...   
23512164                1376  Ping catspeedtest (Private-VLAN10)   
23512165                1376  Ping catspeedtest (Private-VLAN10)   
23512166                1376  Ping catspeedtest (Private-VLAN10)   
23512167                1376  Ping catspeedtest (Private-VLAN10)   
23512168                1376  Ping catspeedtest (Private-VLAN10)   

                                    service.service_uri  \
23512079  /API/REST/Services/v1/Service/1376/Version/16   
23512080  /API/REST/Services/v1/Service/1376/Version/16   
23512081  /API/REST/Services/v1/Service/1376/Version/16   
23512082  /API/REST/Services/v1/Service/1376/Version/16   
23512083  /API/REST/Services/v1/Service/1376/Version/16   
...                                                 ...   
23512164  /API/REST/Services/v1/Service/1376/Version/16   
23512165  /API/REST/Services/v1/Service/1376/Version/16   
23512166  /API/REST/Services/v1/Service/1376/Version/16   
23512167  /API/REST/Services/v1/Service/1376/Version/16   
23512168  /API/REST/Services/v1/Service/1376/Version/16   

          service.service_version service.slt_id target.target_param  \
23512079                       16          

In [47]:
df3['sla_name'].unique()

array(['BV110_NMA', 'BV110_PLK', 'BV110_KKN', 'BV110_RBI', 'BV110_HYI',
       'BV110_SNI', 'BV1100_BRK', 'BV110_PTY', 'ATP-Expansion BRIX',
       'BV110_CMI', 'BV110_NWS',
       'POC-Expansion-SLA_BNG_144_Private (VLAN10)',
       'POC-Expansion-SLA_BRAS_88_Public (VLAN20)'], dtype=object)

In [48]:
table = pd.pivot_table(df3, index=['sla_name', 'status.time_stamp_display'], 
                       columns=['service.service_name',  "target.target_value", "name"], values=["raw_value",])
table

raw_value  \
service.service_name                                                 DNS Test (Private-VLAN10)   
target.target_value                                                                    1.1.1.1   
name                                                                              responseTime   
sla_name                                   status.time_stamp_display                             
ATP-Expansion BRIX                         12/24/2023 11:00 +07                            NaN   
                                           12/24/2023 11:20 +07                            NaN   
                                           12/24/2023 11:40 +07                            NaN   
                                           12/24/2023 12:00 +07                            NaN   
                                           12/24/2023 12:20 +07                            NaN   
...                                                                                        ...   
BV110_SNI                                  12/23/2023 05:00 +07                            NaN   
                                           12/23/2023 16:00 +07                            NaN   
                                           12/23/2023 21:00 +07                            NaN   
POC-Expansion-SLA_BNG_144_Private (VLAN10) 12/25/2023 20:40 +07                            NaN   
POC-Expansion-SLA_BRAS_88_Public (VLAN20)  12/25/2023 20:20 +07                            NaN   

                                                                             \
service.service_name                                                          
target.target_value                                                           
name                                                                 result   
sla_name                                   status.time_stamp_display          
ATP-Expansion BRIX                         12/24/2023 11:00 +07         NaN   
                                           12/24/2023 11:20 +07         NaN   
                                           12/24/2023 11:40 +07         NaN   
                                           12/24/2023 12:00 +07         NaN   
                                           12/24/2023 12:20 +07         NaN   
...                                                                     ...   
BV110_SNI                                  12/23/2023 05:00 +07         NaN   
                                           12/23/2023 16:00 +07         NaN   
                                           12/23/2023 21:00 +07         NaN   
POC-Expansion-SLA_BNG_144_Private (VLAN10) 12/25/2023 20:40 +07         NaN   
POC-Expansion-SLA_BRAS_88_Public (VLAN20)  12/25/2023 20:20 +07         NaN   

                                                                                    \
service.service_name                                                                 
target.target_value                                                  110.78.191.20   
name                                                                  responseTime   
sla_name                                   status.time_stamp_display                 
ATP-Expansion BRIX                         12/24/2023 11:00 +07                NaN   
                                           12/24/2023 11:20 +07                NaN   
                                           12/24/2023 11:40 +07                NaN   
                                           12/24/2023 12:00 +07                NaN   
                                           12/24/2023 12:20 +07                NaN   
...                                                                            ...   
BV110_SNI                                  12/23/2023 05:00 +07                NaN   
                                           12/23/2023 16:00 +07                NaN   
                                           12/23/2023 21:00 +07                NaN   
POC-Expansion-SLA_BNG_144_Private (VLAN10) 12/2

In [49]:
import time
 
# ts stores the time in seconds
ts = int(time.time())
table.to_excel(f"table{ts}.xlsx")

In [ ]:
df3['status'][0]

In [ ]:
df = pd.json_normalize(list_test_status_result, record_path=["test_status_result","status"], meta=[""])
df 

In [ ]:
df.dtypes

In [ ]:
def dict_list_to_df(df, col):
    """Return a Pandas dataframe based on a column that contains a list of JSON objects or dictionaries.
    Args:
        df (Pandas dataframe): The dataframe to be flattened.
        col (str): The name of the column that contains the JSON objects or dictionaries.
    Returns:
        Pandas dataframe: A new dataframe with the JSON objects or dictionaries expanded into columns.
    """

    rows = []
    for index, row in df[col].iteritems():
        for item in row:
            rows.append(item)
    df = pd.DataFrame(rows)
    return df

In [ ]:
df1 = dict_list_to_df(df, "status")
df1

In [ ]:
df2 = dict_list_to_df(df1, "results_scores")
df2

In [ ]:
!pip install flatten-json


In [ ]:
from flatten_json import flatten
df['status_r

In [ ]:
df_flat = pd.io.json.json_normalize(json_struct)
df

In [ ]:
import ast
from pandas.io.json import json_normalize

def only_dict(d):
    '''
    Convert json string representation of dictionary to a python dict
    '''
    return ast.literal_eval(d)

def list_of_dicts(ld):
    '''
    Create a mapping of the tuples formed after 
    converting json strings of list to a python list   
    '''
    return dict([(list(d.values())[1], list(d.values())[0]) for d in ast.literal_eval(ld)])

In [ ]:
A = json_normalize(df['status'].apply(only_dict).tolist()).add_prefix('status.')
A

In [ ]:
pd.json_normalize(list(df['status']))

In [ ]:
new_temp = df.explode('status')
new_temp

In [ ]:
df2 = df.merge(new_temp, left_index=True, right_index=True, suffixes=("_test","_status"))
df2

In [ ]:
df2.to_excel("test.xlsx")

In [ ]:
temp = df.explode('status.results_scores')
temp

In [ ]:
temp

In [ ]:
l1 = []
for l in list_test_status_result:
    l1 = l1 + l['test_status_result']
df = pd.DataFrame(l1)
df = pd.concat([df, df["service"].apply(pd.Series)], axis=1)
df

In [ ]:
df['results_scores']

In [ ]:
import numpy as np

df1 = pd.DataFrame(df['status'][0])
temp_df = pd.DataFrame.from_dict(np.concatenate(df1['results_scores']).tolist())
temp_df[:10]

In [ ]:
final_df = df1.merge(temp_df, how='inner', left_index=True, right_index=True)
final_df


In [ ]:
df = pd.DataFrame(list_test_status_result)
df

In [ ]:
df = df.explode('test_status_result')
df

In [ ]:
l0 = []
for l in list_test_status_result:
    for t in l['test_status_result']:
        for st in t['status']:
            for rs in st['results_scores']:
                temp = t['service'] | (t['target'] or {}) | rs
                temp['sla_name'] = st['sla_name'] 
                temp['time_stamp'] = st['time_stamp']
                temp['time_stamp_display'] = st['time_stamp_display']
                l0.append(temp)
l0[:10]

In [ ]:
list_test_status_result = list(db['exfo_api'].find({}, {'test_status_result':1}))
list_test_status_result

In [ ]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

temp = []
for l in list_test_status_result:
    for d in l['test_status_result']:
        for s in d['status']:
            for rs in s['results_scores']:
                t2 = {rs['name']: [rs['raw_value'], rs['score']]}
                temp.append({**d, **s, **t2})
temp
df = pd.json_normalize(temp)
#df.set_index(['time_stamp_display'], inplace=True)
df['sla_service'] = df['sla_name'] + "/" + df['service_name']
df['sla_service'].unique()

In [ ]:
f = df[df['sla_service'] == 'BV110_CMI/HTTPS Web Performances']
f.set_index(['time_stamp_display'], inplace=True)
f